In [3]:
import pandas as pd

In [92]:
df = pd.read_csv('binding_moad/every.csv',header=None,skiprows=2)
df = df.rename(columns={2:'pdb',3: 'ligand_name', 4: 'ligand_valid', 7: 'affinity_val', 8: 'affinity_unit', 9:'smiles'})
#df = df[df['ligand_valid']!='invalid'].copy()

In [93]:
df['is_sep'] = df[1] == 'Family. Representative Entry is '

In [94]:
df['cum_sum'] = df['is_sep'].cumsum()

In [95]:
from pint import UnitRegistry
ureg = UnitRegistry()

def to_uM(affinity_unit):
    try:
        val = ureg(str(affinity_unit[0])+str(affinity_unit[1]))
        return val.m_as(ureg.uM)
    except Exception:
        pass
    
    try:
        val = ureg(str(affinity_unit[0])+str(affinity_unit[1]))
        return 1/val.m_as(1/ureg.uM)
    except Exception:
        pass

In [96]:
groupby = df.groupby('cum_sum')

In [121]:
def group(df):
    pdb = df[df['is_sep']]['pdb'].values
    if len(pdb) > 0:
        pdb = pdb[0]
        df['pdb_ref'] = pdb
    return df[df['ligand_valid']=='valid']
df_expand = groupby.apply(group).reset_index(drop=True)

In [124]:
df_expand['affinity_uM'] = df_expand[['affinity_val','affinity_unit']].apply(to_uM,axis=1)

In [125]:
df_complex = pd.read_parquet('data/moad_complex.parquet')
df_complex['name'] = df_complex['name'].str.upper()

In [128]:
df_all = df_expand.merge(df_complex,left_on='pdb_ref',right_on='name')

In [129]:
df_all = df_all[~df_all['affinity_val'].isnull()]

In [130]:
df_all

0    1  pdb  ligand_name ligand_valid     5  6  affinity_val  \
0      NaN  NaN  NaN    2PA:C:613        valid    Ki  =          0.62   
2      NaN  NaN  NaN    HAE:C:800        valid    Ki  =          2.60   
7      NaN  NaN  NaN    43W:A:902        valid  ic50  =        580.00   
16     NaN  NaN  NaN    0CG:A:902        valid  ic50  =        770.00   
17     NaN  NaN  NaN    ADN:A:901        valid    Kd  =         15.00   
...    ...  ...  ...          ...          ...   ... ..           ...   
51900  NaN  NaN  NaN  MAN NAG:G:1        valid    Ka  =       7860.00   
51901  NaN  NaN  NaN  MAN NAG:F:1        valid    Ka  =       7860.00   
51902  NaN  NaN  NaN  NGA NAG:F:1        valid    Ka  =       5910.00   
51903  NaN  NaN  NaN  NGA NAG:E:1        valid    Ka  =       5910.00   
51904  NaN  NaN  NaN  NGA NAG:H:1        valid    Ka  =       5910.00   

      affinity_unit                                             smiles  10  \
0                nM                                         NP(=O)(N)O NaN   
2                uM                                           CC(=O)NO NaN   
7                nM                           C#CCCOP(=O)(O)OP(=O)(O)O NaN   
16               nM                            C#CCOP(=O)(O)OP(=O)(O)O NaN   
17               uM  c1nc(c2c(n1)n(cn2)[C@H]3[C@@H]([C@@H]([C@H](O3... NaN   
...             ...                                                ...  ..   
51900          M^-1                                                NaN NaN   
51901          M^-1                                                NaN NaN   
51902          M^-1                                                NaN NaN   
51903          M^-1                                                NaN NaN   
51904          M^-1                                                NaN NaN   

       is_sep  cum_sum pdb_ref  affinity_uM  name  \
0       False        1    6H8J     0.000620  6H8J   
2       False        1    6H8J     2.600000  6H8J   
7       False        2    4S3F     0.580000  4S3F   
16      False        2    4S3F     0.770000  4S3F   
17      False        5    2GL0    15.000000  2GL0   
...       ...      ...     ...          ...   ...   
51900   False    10499    2WDB   127.226463  2WDB   
51901   False    10499    2WDB   127.226463  2WDB   
51902   False    10499    2WDB   169.204738  2WDB   
51903   False    10499    2WDB   169.204738  2WDB   
51904   False    10499    2WDB   169.204738  2WDB   

                                                     seq  
0      NYIVPGEYRVAEGEIEINAGREKTTIRVSNTGDRPIQVGSHIHFVE...  
2      NYIVPGEYRVAEGEIEINAGREKTTIRVSNTGDRPIQVGSHIHFVE...  
7      MEGMRRPTPTVYVGRVPIGGAHPIAVQSMTNTPTRDVEATTAQVLE...  
16     MEGMRRPTPTVYVGRVPIGGAHPIAVQSMTNTPTRDVEATTAQVLE...  
17     MTDMSIKFELIDVPIPQGTNVIIGQAHFIKTVEDLYEALVTSVPGV...  
...                                                  ...  
51900  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
51901  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
51902  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
51903  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
51904  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  

[25425 rows x 17 columns]

In [133]:
df_all[['pdb','ligand_name','smiles','name','affinity_uM','seq']].to_parquet('data/moad.parquet')